In [1]:
import pandas as pd
import numpy as np
import datetime as dt
import json
from datetime import datetime

import plotly.io as pio
import plotly.graph_objects as go
import plotly.express as px
import warnings
from sklearn.cluster import KMeans

warnings.filterwarnings('ignore')

pio.renderers.default = "notebook"
pio.templates.default = "plotly_white"


# this enables relative path imports
import os
from dotenv import load_dotenv
load_dotenv()
_PROJECT_PATH: str = os.environ["_project_path"]
_PICKLED_DATA_FILENAME: str = os.environ["_pickled_data_filename"]

import sys
from pathlib import Path
project_path = Path(_PROJECT_PATH)
sys.path.append(str(project_path))

import config_v2 as cfg

from library_report_v2 import Cleaning as cln
from library_report_v2 import Graphing as grp
from library_report_v2 import Processing as pro
from library_report_v2 import Configuration as repcfg

In [2]:
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [3]:
periodo_historico = cfg.BASELINE
periodo_de_estudio = cfg.STUDY

In [4]:
def show_response_contents(df):
    print("The response contains:")
    print(json.dumps(list(df['variable'].unique()), sort_keys=True, indent=4))
    print(json.dumps(list(df['device'].unique()), sort_keys=True, indent=4))

In [5]:
df = pd.read_pickle(project_path / 'data' / _PICKLED_DATA_FILENAME)

In [6]:
df = df.sort_values(by=['variable','datetime'])
df = pro.datetime_attributes(df)

In [7]:
df_chiller = df.copy()
df_chiller = df_chiller[df_chiller['variable'].isin(['eficiencia-chiller','factor-de-potencia','potencia-termica','potencia-activa','factor-carga-chiller'])]

In [8]:
df_chiller = df_chiller[df_chiller['device'].isin(['cvl---chiller'])]
#df_chiller_2 = df_chiller.copy()

### Rendimientos Chiller

In [9]:
df_grouped = df_chiller.groupby(['hour', 'variable']).median().reset_index()

df_pivot = df_chiller.pivot(columns='variable', values='value')


In [10]:
import pandas as pd
import plotly.express as px


df_pivot = df_chiller.pivot(columns='variable', values='value')

# Suponiendo que ya tienes df_pivot sin duplicados
# Filtra los valores mayores a 0

#df_filtered = df_pivot[(df_pivot['potencia-activa'] > 0) & (df_pivot['eficiencia-chiller'] > 0)]

In [21]:
import plotly.express as px
from sklearn.cluster import KMeans

# Filtrar los datos
df_filtered = df_pivot[(df_pivot['potencia-activa'] >= 50) & (df_pivot['eficiencia-chiller'] >=0.4 ) & (df_pivot['eficiencia-chiller'] <=2 )]

# Aplicar K-Means para agrupar los datos por potencia activa
kmeans = KMeans(n_clusters=3)  
df_filtered['cluster'] = kmeans.fit_predict(df_filtered[['eficiencia-chiller']])

# Crear un gráfico de dispersión con colores de acuerdo a los clusters
figx = px.scatter(df_filtered, x='potencia-activa', y='eficiencia-chiller', trendline='ols', color='cluster', 
                  color_continuous_scale='viridis')

# Actualizar el título y las etiquetas
figx.update_layout(title='Relación entre Rendimiento Chiller y Potencia Activa', xaxis_title='Potencia Activa [kW]', 
                   yaxis_title='Rendimiento Chiller [kW/TR]')

# Mostrar el gráfico
figx.show()


In [22]:
# Filtrar los datos
df_filtered_2 = df_pivot[(df_pivot['potencia-termica'] >=40 ) & (df_pivot['potencia-termica'] <=300 ) & (df_pivot['eficiencia-chiller'] >=0.4 ) & (df_pivot['eficiencia-chiller'] <=2 )]

# Aplicar K-Means para agrupar losr datos por potencia activa
kmeans = KMeans(n_clusters=4)  # Puedes ajustar el número de clusters según tu preferencia
df_filtered_2['cluster'] = kmeans.fit_predict(df_filtered_2[['eficiencia-chiller']])

# Crear un gráfico de dispersión con colores de acuerdo a los clusters
figx = px.scatter(df_filtered_2, x='potencia-termica', y='eficiencia-chiller', trendline='ols', color='cluster', 
                  color_continuous_scale='viridis')

# Actualizar el título y las etiquetas
figx.update_layout(title='Relación entre Rendimiento Chiller y Potencia termica', xaxis_title='Potencia Termica [TR]', 
                   yaxis_title='Rendimiento Chiller [kW/TR]')

# Mostrar el gráfico
figx.show()

In [23]:
# Filtrar los datos
df_filtered_1 = df_pivot[(df_pivot['potencia-activa'] >= 40) & (df_pivot['potencia-termica'] >=40 ) & (df_pivot['potencia-termica'] <=300 )]

# Aplicar K-Means para agrupar los datos por potencia termica
kmeans = KMeans(n_clusters=3)  # Puedes ajustar el número de clusters según tu preferencia
df_filtered_1['cluster'] = kmeans.fit_predict(df_filtered_1[['potencia-termica']])

# Crear un gráfico de dispersión con colores de acuerdo a los clusters
figx = px.scatter(df_filtered_1, x='potencia-activa', y='potencia-termica', trendline='ols', color='cluster', 
                  color_continuous_scale='viridis')

# Actualizar el título y las etiquetas
figx.update_layout(title='Relación entre Potencia Termica y Potencia Activa', xaxis_title='Potencia Activa [kW]', 
                   yaxis_title='Potencia Termica [TR]')

# Mostrar el gráfico
figx.show()
